In [1]:
import pandas as pd
from splink.exploratory import completeness_chart
from splink import DuckDBAPI, block_on
from splink import SettingsCreator, Linker
import splink.comparison_library as cl
from splink.blocking_analysis import (
    cumulative_comparisons_to_be_scored_from_blocking_rules_chart,
)
import os
import numpy as np
db_api = DuckDBAPI()

from linkage_model import LinkageModel
from cleaning_fx import format_procurement, format_finance

# Load Datasets

In [2]:
data_path = "data/"
a_company = pd.read_csv(os.path.join(data_path, "a__company.csv"))
a_geo = pd.read_csv(os.path.join(data_path, "a__geo.csv"))

b_company = pd.read_csv(os.path.join(data_path, "b__company.csv"))
b_hierarchy = pd.read_csv(os.path.join(data_path, "b__hierarchy.csv"))
b_address = pd.read_csv(os.path.join(data_path, "b__address.csv"),
    dtype={11: str, 15: str})

In [3]:
a_clean = format_procurement(a_company, a_geo)
b_clean = format_finance(b_company, b_hierarchy, b_address)

# Visualize completeness for column selection

In [4]:
completeness_chart(a_clean, db_api=db_api)

alt.LayerChart(...)

In [5]:
completeness_chart(b_clean, db_api=db_api)

alt.LayerChart(...)

In [6]:
used_columns = ['unique_id', 'name', 'iso', 'state', 'city', 'zipcode', 'address_number', 'street_name', 'websiteurl', 'area_code']

a_used = a_clean[used_columns]
a_used.head(50)

unique_id                                 name iso        state  \
9651    18802368     lohberger engineering pty ltdsjf  us          NaN   
67057   18802818                      lockheed martin  us           mn   
31323   18802831                                logus  us  not_defined   
22669   18804109                      lockheed martin  us           nj   
18784   18883986                              lugokdc  us           wa   
9397    18884006              lockheed martin gyrocam  us                
20023   18885103             l3 global communications  us           ny   
72198   18889982                   levin professional  us           md   
21208   18890128                           lepier oil  us           mn   
3401    18890131                      linc government  us           ky   
13903   18890248                    l3 communications  us           tx   
52638   18890314                    lone star pavment  us           tx   
5738    18890351                    los angeles foods  us           ca   
28272   18890523                               lawson  us           il   
13574   18890765                   life of leadership  us           nv   
36528   18890919                       lotek wireless  ca      ontario   
42255   18891008                   leica microsystems  us           il   
28156   18891031                  lockheed martin ms2  us           nj   
30581   18891332                    layne christensen  us           tx   
21347   18908201                      lockheed martin  us           az   
12053   18908231                      lockheed martin  us           md   
1103    18908234                      lockheed martin  us                
17589   18908391                        lobo ventures  us           tx   
43968   18908641                       lego education  us           ks   
44179   18908644                                 lord  us           pa   
14367   18908687                        linear motion  us           mi   
15401   18908769                       lbb associates  us           md   
31379   18908948                               laurus  us           md   
6203    18909177                      lilly tree farm  us           il   
15059   18909758     livingstone general construction  us           ca   
17637   18909830                                  lee  us           ca   
19216   18914626                    l3 communications  us           ga   
42544   18914911  lewis sound and video professionals  us           wi   
22720   18915023                    l3 communications  us           nj   
43389   18915292          lt engineering construction  us           md   
31674   18915357                            luminator  us           tx   
29733   18915934                            logistics  us           va   
32358   18928857                      lockheed martin  us  not_defined   
23162   18946910                        leggett platt  us           il   
6761    18946943                logistics engineering  us           md   
890     18947216                             la foods  us  not_defined   
30201   18947312                  learning associates  us           il   
48177   18947317                    luther consulting  us           in   
48548   18947454                      lockheed martin  us                
67169   18947538                                  lrk  us           ia   
31199   18947782                                 loos  us                
17752   18948445                      liberty roofing  us           az   
19853   18949309                        l c engineers  us           nj   
26197   18949408          laucks testing laboratories  us          NaN   
15247   18949454                                   l3  us           ia   

                 city zipcode address_number  \
9651              NaN     NaN            NaN   
67057      saint paul   55121            NaN   
31323     not_defined   34409            NaN   
22669      moorestown   08057           

In [7]:
b_used = b_clean[used_columns]
b_used.head(50)

unique_id                               name  iso state          city  \
0    000BFG-E                            lotsoff   us    tx   san antonio   
14   000FF7-E                             legacy   us    ca       fremont   
7    000FJL-E                        leadingside   us    ma     cambridge   
15   000HNQ-E                     lci industries   us    in       elkhart   
16   000HNW-E                          lasercard   us    ca      mountain   
19   000JF6-E                            longwen   us    az    scottsdale   
3    000JP9-E                       leonardo spa   it                rome   
6    000L15-E                            lisi sa   fr    fc       belfort   
22   000NY4-E                      lumara health   us    mo  chesterfield   
8    000NY7-E                            la gear   us    ca   los angeles   
9    000NY8-E                     la quinta inns   us    tx   san antonio   
10   000NY9-E               la quinta motor inns   us    tx   san antonio   
11   000NYB-E                           la z boy   us    mi        monroe   
13   000NYC-E                            labarge   us    mo         louis   
33   000NYD-E                         labone old   us    ks           NaN   
34   000NYF-E              laboratory of america   us    nc    burlington   
35   000NYG-E                        laclede gas   us    mo         louis   
36   000NYH-E                      laclede steel   us    mo         louis   
44   000NYJ-E                  lacrosse footwear   us    or      portland   
56   000NYK-E                 la z boy casegoods   us    mi       raleigh   
57   000NYL-E                      ladysmith iga   us   NaN           NaN   
58   000NYM-E                      ladysmith iga   us   NaN           NaN   
64   000NYN-E                    lafarge america   us    il       chicago   
66   000NYP-E                   laidlaw covenant   us    ny           NaN   
67   000NYQ-E                             laifer   us    ny           NaN   
77   000NYR-E                 lake ariel bancorp   us    pa    lake ariel   
80   000NYS-E                               lake   us   NaN           NaN   
81   000NYT-E                 lake shore bancorp   us    ny       dunkirk   
97   000NYV-E                           lakeland   us    in        warsaw   
98   000NYW-E                lakeland industries   us    ny      new york   
105  000NYX-E                           lakeside   us    ga           NaN   
107  000NYZ-E                                lam   us    ca       fremont   
108  000NZ0-E             lambert communications   us   NaN           NaN   
117  000NZ2-E                             lamcor   us    mn      le sueur   
125  000NZ3-E                    lamonts apparel   us    wa      kirkland   
126  000NZ4-E                    lamson sessions   us    oh     beachwood   
128  000NZ5-E                   lancaster colony   us    oh   westerville   
137  000NZ6-E                              lance   us    nc     charlotte   
138  000NZ7-E                             lancer   us    tx   san antonio   
139  000NZ8-E                lancer orthodontics   us    ca         vista   
147  000NZB-E                           landauer   us    il      glenwood   
148  000NZH-E          legg mason partners money   us    ny      new york   
149  000NZJ-E                  landmark graphics   us    tx       houston   
155  000NZK-E     landmark institutional funds i  NaN   NaN           NaN   
157  000NZL-E  legg mason partners institutional   us    ny      new york   
158  000NZM-E         legg mason partners global   us   NaN           NaN   
166  000NZP-E  legg mason partners premium money   us    ny      new york   
169  000NZT-E                            landrys   us    tx       houston   
170  000NZV-E                          lands end   us    wi    dodgeville   
178  000NZW-E                   landsing pacific   us    ca     san mateo   

       zipcode address_number                       street_name  \
0    7820

# Determine Blocking Methodology

From these plots, I can see that the following variables appear to be good candidates:
- iso would make a good blocking variable
- company name comparison is key
- comparing addresses might give more information (although a lot of data is missing)
- city, state, and zip code are also missing information but still might be useful 

What do I want to see from blocking rules?
- < 10M added comparisons for each block
- Compare highly specific blocks first, then move to more generalized blocks

In [8]:
blocking_rules = [

    # Highly specific blocks
    block_on("zipcode", "area_code"),
    block_on("state", "city", "area_code"),
    block_on("state", "city"),
    block_on("name", "iso"),
    block_on("street_name", "iso"),

    # Moderately specific blocks
    block_on("state", "area_code"),
    block_on("city", "area_code"),       
    block_on("city"),                    
    block_on("zipcode"),


    # General fallback blocks
    block_on("LEFT(zipcode, 3)"),
    block_on("area_code"),
    block_on("LEFT(name, 8)", "iso"),
]

cumulative_comparisons_to_be_scored_from_blocking_rules_chart(
    table_or_tables=[a_used, b_used],
    blocking_rules=blocking_rules,
    db_api=db_api,
    link_type="link_only"
)

alt.Chart(...)

# Initialize Linkage Model

In [9]:
linkage_model = LinkageModel(a_used, b_used)

# Train Linkage Model

In [10]:
linkage_model.fit()

----- Estimating u probabilities using random sampling -----

Estimated u probabilities using random sampling

Your model is not yet fully trained. Missing estimates for:
    - name (no m values are trained).
    - street_name (no m values are trained).
    - websiteurl (no m values are trained).
    - address_number (no m values are trained).
    - zipcode (no m values are trained).
    - area_code (no m values are trained).
    - iso (no m values are trained).

----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
(l."state" = r."state") AND (l."city" = r."city")

Parameter estimates will be made for the following comparison(s):
    - name
    - street_name
    - websiteurl
    - address_number
    - zipcode
    - area_code
    - iso

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 

Iteration 1: Largest change in params was -0.678 in the m_probability of name, level `Exact m

In [11]:
settings = linkage_model.linker.misc.save_model_to_json(
    "trained_model.json", overwrite=True
)

In [12]:
linkage_model.linker.visualisations.match_weights_chart()

alt.VConcatChart(...)

In [13]:
linkage_model.linker.evaluation.unlinkables_chart()

alt.LayerChart(...)

# Predict using trained model

In [14]:
pred_df = linkage_model.predict()
pred_df.head()

Blocking time: 6.30 seconds
Predict time: 12.10 seconds


match_weight  match_probability         source_dataset_l  \
0     -0.535955           0.408180  __splink__input_table_0   
1     -2.612577           0.140529  __splink__input_table_0   
2     -2.612577           0.140529  __splink__input_table_0   
3     -4.014822           0.058257  __splink__input_table_0   
4     -3.754520           0.068982  __splink__input_table_0   

          source_dataset_r unique_id_l unique_id_r  \
0  __splink__input_table_1    51682359    0DF6DL-E   
1  __splink__input_table_1    51682426    0DF6DL-E   
2  __splink__input_table_1    51682457    0DF6DL-E   
3  __splink__input_table_1    51708811    0DZJ9Q-E   
4  __splink__input_table_1    51709201    0DZJ9Q-E   

                                              name_l                 name_r  \
0          lanier parking solution atlanta fulton ga                lumense   
1                   lanier parking atlanta fulton ga                lumense   
2  latin american translators network latn atlant...                lumense   
3                                   leftwich ludaway  lindsay reishman real   
4                                        life stride  lindsay reishman real   

   gamma_name   bf_name  ... gamma_iso  tf_iso_l  tf_iso_r    bf_iso  \
0           0  0.976712  ...         1  0.502893  0.502893  3.142499   
1           0  0.976712  ...         1  0.502893  0.502893  3.142499   
2           0  0.976712  ...         1  0.502893  0.502893  3.142499   
3           0  0.976712  ...         1  0.502893  0.502893  3.142499   
4           0  0.976712  ...         1  0.502893  0.502893  3.142499   

  bf_tf_adj_iso state_l  state_r      city_l      city_r match_key  
0      0.632708      ga       ga     atlanta     atlanta         1  
1      0.632708      ga       ga     atlanta     atlanta         1  
2      0.632708      ga       ga     atlanta     atlanta         1  
3      0.632708      dc       dc  washington  washington         1  
4      0.632708      dc       dc  washington  washington         1  

[5 rows x 48 columns]

In [15]:
records_to_view = linkage_model.predictions.as_record_dict(limit=1000)
linkage_model.linker.visualisations.waterfall_chart(records_to_view, filter_nulls=False)

alt.LayerChart(...)

In [25]:
def filter_and_save(df, a_used):

    # Sort by unique_id_l and match_probability (descending)
    sorted_df = df.sort_values(['unique_id_l', 'match_probability'], 
                                   ascending=[True, False])
    
    # Keep only the first row (highest probability) for each unique_id_l
    filtered_df = sorted_df.groupby('unique_id_l').first().reset_index()

    # Keep only the first row (highest probability) for each vendor_id and create the final df to save
    filtered_df = sorted_df.groupby('unique_id_l').first().reset_index()
    final_df = pd.DataFrame({
    'vendor_id': filtered_df['unique_id_l'],
    'entity_id': filtered_df['unique_id_r'],
    'confidence_of_match': filtered_df['match_probability']
    })

    # Add unmatched vendor_ids from a_used
    all_vendor_ids = set(a_used['unique_id'])
    matched_vendor_ids = set(final_df['vendor_id'])
    unmatched_vendor_ids = all_vendor_ids - matched_vendor_ids

    unmatched_df = pd.DataFrame({
        'vendor_id': list(unmatched_vendor_ids),
        'entity_id': pd.NA,
        'confidence_of_match': pd.NA
    })

    # Append unmatched vendors to the final result
    final_df = pd.concat([final_df, unmatched_df], ignore_index=True)

    return final_df

In [26]:
final_df = filter_and_save(pred_df, a_used)
final_df.head(100)

C:\Users\tomss\AppData\Local\Temp\ipykernel_9576\4071308476.py:30: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_df = pd.concat([final_df, unmatched_df], ignore_index=True)


vendor_id entity_id  confidence_of_match
0   112250392  0DBVHK-E             0.122661
1   112250395  07313Z-E             1.000000
2   112250405  07Q85P-E             0.762180
3   112250415  086C4Y-E             0.339120
4   112250448  0GQCHK-E             0.537291
..        ...       ...                  ...
95  133569342  0CCJ5R-E             0.993301
96  133570108  0DG2ZM-E             0.643356
97  133572773  080JFC-E             0.991736
98  133583359  00BLJ1-E             0.501952
99  133583411  06X58G-E             0.999908

[100 rows x 3 columns]

In [27]:
# Save the result as a .csv
final_df.to_csv("linked_entities.csv", index=False)
print("results have been saved as linked_entities.csv")

results have been saved as linked_entities.csv
